<a href="https://colab.research.google.com/github/mindyng/Covid19/blob/master/Study_Annotations_Models.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [31]:
!pip install tokenizer

     |████████████████████████████████| 112kB 3.4MB/s 


In [32]:
import pandas as pd
import numpy as np
import spacy
import gensim

import nltk;  nltk.download('stopwords') #Why are there 3 stopwods calls?
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

from nltk.tokenize import word_tokenize
import nltk
nltk.download('punkt')
import tokenizer

nlp = spacy.load('en', disable=['parser', 'ner'])

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [1]:
from google.colab import files
files.upload()

Saving NLPDatasets_v7_preprocessed_v7_dataset.csv to NLPDatasets_v7_preprocessed_v7_dataset.csv


{'NLPDatasets_v7_preprocessed_v7_dataset.csv': b'paper_id,section,text\n08a40e31fde744729050ab037f80aa67c7d1053f,title,Global versus focused isolation during the SARS-CoV-2 pandemic- A cost-effectiveness analysis\n08a40e31fde744729050ab037f80aa67c7d1053f,abstract,Background: The novel coronavirus (SARS-CoV-2) pandemic is driving many countries to adopt global isolation measures in an attempt to slow-down its spread. These extreme measures are associated with extraordinary economic costs.\n08a40e31fde744729050ab037f80aa67c7d1053f,introduction,"Since its identification at the very end of 2019, the novel coronavirus (SARS-CoV-2) has been spreading around the world at an extraordinary speed and is now officially declared as a pandemic"\n08a40e31fde744729050ab037f80aa67c7d1053f,introduction,"(1). Following China, many countries around the world have adopted social distancing measures largely based on quarantine and travel bans, as well as on isolation of infected patients and their close co

In [72]:
NLPData = pd.read_csv('NLPDatasets_v7_preprocessed_v7_dataset.csv')
NLPData

paper_id  ...                                               text
0     08a40e31fde744729050ab037f80aa67c7d1053f  ...  Global versus focused isolation during the SAR...
1     08a40e31fde744729050ab037f80aa67c7d1053f  ...  Background: The novel coronavirus (SARS-CoV-2)...
2     08a40e31fde744729050ab037f80aa67c7d1053f  ...  Since its identification at the very end of 20...
3     08a40e31fde744729050ab037f80aa67c7d1053f  ...  (1). Following China, many countries around th...
4     08a40e31fde744729050ab037f80aa67c7d1053f  ...  However, a few countries, such as South Korea,...
...                                        ...  ...                                                ...
9144  c209c6c9d7c022e0c4b997e2d942c0928eac537c  ...                                 -NC-ND 4.0 license
9145  c209c6c9d7c022e0c4b997e2d942c0928eac537c  ...                                                 []
9146  c209c6c9d7c022e0c4b997e2d942c0928eac537c  ...  epidemic, African migrants residing in Wuhan, ...
9147  c209c6c9d7c022e0c4b997e2d942c0928eac537c  ...  African community organisations also compile a...
9148  c209c6c9d7c022e0c4b997e2d942c0928eac537c  ...  Correspondence www.thelancet.com/public-health...

[9149 rows x 3 columns]

In [73]:
#Group rows by paper_id
NLPData2 = NLPData.drop(['section'], axis=1)
NLPData2['text'] = NLPData2['text'].fillna('').astype(str)
NLPData2 = NLPData2.groupby('paper_id')['text'].apply(' '.join).reset_index()
NLPData2

paper_id                                               text
0    01ceb817f8665ed0047c4675e04b67b199e18832  Journal Pre-proof The Chinese herbal prescript...
1    023aa7bdf9b73b7453051e8fd33f9e80df951001   [] That same day, the Coronavirus Study Group...
2    0329e0f2e3b8ab0eabe2afe0e5214cc88c61080e  Journal Pre-proof Favipiravir, an anti-influen...
3    038d47e5e2526b54dd06cb90340d99b0252b90e7  Association of radiologic findings with mortal...
4    04fae0c0195e39e5bcfb0ddb7a56d4e22944e28f  Journal Pre-proof Novel decoy cellular vaccine...
..                                        ...                                                ...
311  fd14ed7c073b7ff03afa517e9c0fd1e849878252  Direct RNA sequencing and early evolution of S...
312  fe297e7210ed7586d1d84f774ca15a60b5e70173  Coronavirus (COVID-19) Outbreak: What the Depa...
313  fede3c3576d09710757e066a2315889044118c55  Integrated infection control strategy to minim...
314  ff9b8ea0d7aeaf02cbe9943601c0d00ae0aefd93  Investigation of three clusters of COVID-19 in...
315  ffcead8e90594fc809376dc58dcf72e2d1951f9e  The target landscape of N4-hydroxycytidine bas...

[316 rows x 2 columns]

In [74]:
NLPData2['text'][0] #Check

"Journal Pre-proof The Chinese herbal prescription JZ-1 induces autophagy to protect against herpes simplex Virus-2 in human vaginal epithelial cells by inhibiting the PI3K/Akt/mTOR pathway The Chinese herbal prescription JZ-1 induces autophagy to protect against herpes simplex Virus-2 in human vaginal epithelial cells by inhibiting the PI3K/Akt/mTOR pathway, Journal of Ethnopharmacology (2020), doi: https://doi. Genital herpes is one of the most common, persistent and highly contagious The results were analyzed by the 2 −∆∆CT method with β-actin as an internal control. The sequences of the primers used in this study are listed in Table 2 . anti-p-mTOR, anti-mTOR, anti-gD, anti-ICP5 and anti-β-actin) at 4°C. After washing 267 three times with TBST for 10 min each, the membranes were incubated with 268 secondary antibodies for 1 h at room temperature, washed another three times, and 269 then visualized by an Odyssey Infrared Imaging system (LI-COR Biosciences, USA). The band densities w

In [75]:
#Lowercase all letters, get rid of punctuation, get rid of extra spaces on left and right side of string
import string
NLPData2['text'] = NLPData2['text'].map(lambda x: x.lower().translate(str.maketrans('', '', string.punctuation)).strip())
NLPData2['text'][0] #got rid of abbreviations, cool!

'journal preproof the chinese herbal prescription jz1 induces autophagy to protect against herpes simplex virus2 in human vaginal epithelial cells by inhibiting the pi3kaktmtor pathway the chinese herbal prescription jz1 induces autophagy to protect against herpes simplex virus2 in human vaginal epithelial cells by inhibiting the pi3kaktmtor pathway journal of ethnopharmacology 2020 doi httpsdoi genital herpes is one of the most common persistent and highly contagious the results were analyzed by the 2 −∆∆ct method with βactin as an internal control the sequences of the primers used in this study are listed in table 2  antipmtor antimtor antigd antiicp5 and antiβactin at 4°c after washing 267 three times with tbst for 10 min each the membranes were incubated with 268 secondary antibodies for 1 h at room temperature washed another three times and 269 then visualized by an odyssey infrared imaging system licor biosciences usa the band densities were quantified by imagej national institut

In [76]:
#Remove non-ASCII characters
NLPData2['text'].replace({r'[^\x00-\x7F]+':''}, regex=True, inplace=True)
NLPData2['text'][0]

'journal preproof the chinese herbal prescription jz1 induces autophagy to protect against herpes simplex virus2 in human vaginal epithelial cells by inhibiting the pi3kaktmtor pathway the chinese herbal prescription jz1 induces autophagy to protect against herpes simplex virus2 in human vaginal epithelial cells by inhibiting the pi3kaktmtor pathway journal of ethnopharmacology 2020 doi httpsdoi genital herpes is one of the most common persistent and highly contagious the results were analyzed by the 2 ct method with actin as an internal control the sequences of the primers used in this study are listed in table 2  antipmtor antimtor antigd antiicp5 and antiactin at 4c after washing 267 three times with tbst for 10 min each the membranes were incubated with 268 secondary antibodies for 1 h at room temperature washed another three times and 269 then visualized by an odyssey infrared imaging system licor biosciences usa the band densities were quantified by imagej national institutes of 

In [77]:
#Tokenize
NLPData2['text'] = NLPData2['text'].map(lambda x: x.split())
NLPData2['text']

0      [journal, preproof, the, chinese, herbal, pres...
1      [that, same, day, the, coronavirus, study, gro...
2      [journal, preproof, favipiravir, an, antiinflu...
3      [association, of, radiologic, findings, with, ...
4      [journal, preproof, novel, decoy, cellular, va...
                             ...                        
311    [direct, rna, sequencing, and, early, evolutio...
312    [coronavirus, covid19, outbreak, what, the, de...
313    [integrated, infection, control, strategy, to,...
314    [investigation, of, three, clusters, of, covid...
315    [the, target, landscape, of, n4hydroxycytidine...
Name: text, Length: 316, dtype: object

In [78]:
# Remove stop words
stop_words = stopwords.words('english')
NLPData2['text'].apply(lambda x: [item for item in x if item not in stop_words])

0      [journal, preproof, chinese, herbal, prescript...
1      [day, coronavirus, study, group, csg, internat...
2      [journal, preproof, favipiravir, antiinfluenza...
3      [association, radiologic, findings, mortality,...
4      [journal, preproof, novel, decoy, cellular, va...
                             ...                        
311    [direct, rna, sequencing, early, evolution, sa...
312    [coronavirus, covid19, outbreak, department, r...
313    [integrated, infection, control, strategy, min...
314    [investigation, three, clusters, covid19, sing...
315    [target, landscape, n4hydroxycytidine, based, ...
Name: text, Length: 316, dtype: object

In [0]:
#Lemmatize
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    
    doc = nlp(texts) 
    texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out
NLPData2['text']=NLPData2['text'].map(lambda x: lemmatization(x))

In [0]:
#Rejoin words as a huge string with ''.join()

In [0]:
#Put Pre-Process in Function
# def preprocess(textCol):
